---
title: "🗓️ Week 4 - Classification & Metrics & Resampling Methods"
subtitle: "Theme: Supervised Learning"
author: "Dr. Ghita Berrada"
date: "14 February 2025"
format: 
  html:
    from: markdown+emoji
    page-layout: full
    toc: true
    toc-depth: 2
self-contained: true
---

Welcome to Week 4! This week, we go back to classification. But, before we start, let's do a bit of set up

⚙️ Set up

**Loading Python libraries**

In [1]:
import numpy as np
import pandas as pd
from sklearn.metrics import confusion_matrix, precision_score, recall_score, accuracy_score,f1_score,balanced_accuracy_score
from sklearn.neighbors import KNeighborsClassifier
import statsmodels.api as sm
import sweetviz as sv
import missingno as msno
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import LabelEncoder
import matplotlib.pyplot as plt
import seaborn as sns
from lets_plot import *
LetsPlot.setup_html()

# Part 1: A tennis match outcome prediction problem

## Introducing the dataset

In this part, we'll be looking at a dataset about tennis^[credit to Vignesh for the idea thanks to his mention of GOAT on Slack😉]. The data contains match stats and player info for WTA (Women's Tennis Association) and ATP (Association of Tennis Professionals) between 1949 and 2021. The data is available on [Kaggle](https://www.kaggle.com/datasets/taylorbrownlow/atpwta-tennis-data?resource=download) and was originally sourced from [Jeff Sackmann's GitHub repository](https://github.com/JeffSackmann/tennis_atp) (which maintains the dataset and updates it on a regular basis).

In [5]:
df = pd.read_csv('../data/KaggleMatches.csv',low_memory=False)

For simplicity, we'll filter the original dataset so as to only retain ATP data. 

In [6]:
# filtering to only retain ATP data
df=df.query("league=='atp'")

We'll also filter the data to only retain data from 1969 onwards. 

Any ideas as to why we do that? 

And how do we do that?

Let's have a look at our data:

In [ ]:
report = sv.analyze(filtered_df)
report.show_notebook() 

What features do you think we can remove straight away? Why? Which should we transform for modeling purposes?



## 1.2 Before we continue: a recap on logistic regression

Consider a **binary** response:

$$
Y = \begin{cases}
0 \\
1
\end{cases}
$$

We model the probability that $Y = 1$ using the **logistic function** (aka. sigmoid curve):

$$
Pr(Y = 1|X) = p(X) = \frac{e^{\beta_0 + \beta_1X}}{1 + e^{\beta_0 + \beta_1 X}}
$$

This function is mathematically guaranteed to be bounded by the interval $[0, 1]$.

### 1.1.1 Insights into the logistic regression function

Let's see how this mathematical function looks like:

In [ ]:
def plot_logistic_function(X_range, beta0_values, beta1_values, color=None):
    # Create a dataframe similar to expand.grid() in R
    df = pd.DataFrame(
        [(X, beta0, beta1) for X in X_range for beta0 in beta0_values for beta1 in beta1_values],
        columns=['X', 'beta0', 'beta1']
    )

    # Compute logistic function
    df['Y'] = np.exp(df['beta0'] + df['beta1'] * df['X']) / (1 + np.exp(df['beta0'] + df['beta1'] * df['X']))

    # Convert to categorical for ordered factors
    df['beta0'] = df['beta0'].astype(str)
    df['beta1'] = df['beta1'].astype(str)

    # Choose color mapping
    if color is None:
        p = ggplot(df, aes(x='X', y='Y'))
    elif color == "beta0":
        p = ggplot(df, aes(x='X', y='Y', color='beta0', linetype='beta0'))
    else:
        p = ggplot(df, aes(x='X', y='Y', color='beta1', linetype='beta1'))

    # Add lines and customize appearance
    p += geom_line(size=1.4) + \
        ggsize(800, 400) + \
        labs(x="X", y="Y") + \
        theme(panel_grid_minor='blank') + \
        theme(axis_title=element_text(size=24), 
              axis_text=element_text(size=18), 
              legend_text=element_text(size=18),
              legend_position="right")

    return p

In [ ]:
X_range = np.linspace(-400, 400, 100)
beta0_values = [-3, 0, 1]
beta1_values = [1, 1, 1]
p=plot_logistic_function(X_range, beta0_values, beta1_values, color="beta1")
p+=ggtitle("If I keep beta1 constant and equal to 1 and vary beta0")
p

In [ ]:
X_range = np.linspace(-4, 4, 100)
beta0_values = [0, 0, 0, 0]
beta1_values = [-1, 0, 1, 2]

p=plot_logistic_function(X_range, beta0_values, beta1_values, color="beta1")
p+=ggtitle("If I keep beta0 constant and equal to 0 and vary beta1")
p

## 1.2 Going back to our match prediction problem

I, on the sly, define my tennis match lose/win prediction problem as a binary class prediction problem: the winner is the player with the most ranking points (regardless of his name!). My outcome variable is the aptly named `outcome`.

I have temporal data so I can't do my training/test split as usual. I'll keep data prior to 2020 as training data and data posterior to 2020 as test data

In [ ]:
train_df = filtered_df[filtered_df['tourney_date'] < '2020-01-01']
test_df = filtered_df[filtered_df['tourney_date'] >= '2020-01-01']

Let's try and fit a logistic regression model on the training data:

```{r}

```


```text
Optimization terminated successfully.
         Current function value: 0.607134
         Iterations 5
                           Logit Regression Results                           
==============================================================================
Dep. Variable:                outcome   No. Observations:                 6671
Model:                          Logit   Df Residuals:                     6644
Method:                           MLE   Df Model:                           26
Date:                Fri, 14 Feb 2025   Pseudo R-squ.:                 0.05360
Time:                        12:02:41   Log-Likelihood:                -4050.2
converged:                       True   LL-Null:                       -4279.6
Covariance Type:            nonrobust   LLR p-value:                 1.131e-80
===============================================================================
                  coef    std err          z      P>|z|      [0.025      0.975]
-------------------------------------------------------------------------------
const           0.5121      0.127      4.029      0.000       0.263       0.761
surface         0.0555      0.031      1.778      0.075      -0.006       0.117
winner_hand     0.0271      0.077      0.352      0.725      -0.124       0.178
winner_ht       0.0476      0.026      1.819      0.069      -0.004       0.099
winner_age     -0.0481      0.027     -1.812      0.070      -0.100       0.004
loser_hand     -0.0489      0.077     -0.637      0.524      -0.199       0.102
loser_ht       -0.0157      0.027     -0.588      0.557      -0.068       0.037
loser_age       0.1104      0.028      3.974      0.000       0.056       0.165
best_of         0.0378      0.039      0.976      0.329      -0.038       0.114
w_ace           0.1015      0.035      2.922      0.003       0.033       0.170
...
l_SvGms        -0.4567      0.216     -2.115      0.034      -0.880      -0.034
l_bpSaved       0.0705      0.167      0.423      0.672      -0.256       0.397
l_bpFaced      -0.0584      0.196     -0.298      0.766      -0.443       0.326
===============================================================================
```

What does this tell me?

- If variables were 0, the log-odds of a win increases by the intercept i.e 0.5121.

The probability of a win increases by:

In [ ]:
log_odds = 0.5121
probability = 1 / (1 + np.exp(-log_odds))
print(probability)

- If all other predictors are held constant, wach additional ace hit by the winner increases the odds of winning bu 0.1015 and the probability of winning increases by:

In [ ]:
w_ace = 1
w_ace_coef = 0.1015
new_log_odds = 0.5121 + (w_ace_coef * w_ace)

probability_w_ace_1 = 1 / (1 + np.exp(-new_log_odds))
print(probability_w_ace_1)

How should I go about evaluating the performance of my model?

In [ ]:
X_test = test_df.drop(columns=["outcome","tourney_name","winner_name","loser_name","tourney_level",'round','winner_rank','winner_rank_points','loser_rank','loser_rank_points','tourney_date'], axis=1).astype(float)
X_test = sm.add_constant(X_test)
y_test = test_df["outcome"].astype(int)

y_pred = logit_model.predict(X_test)

# Convert probabilities to binary outcome (0 or 1) using threshold of 0.5
y_pred_binary = (y_pred > 0.5).astype(int)

# Confusion Matrix
conf_matrix = confusion_matrix(y_test, y_pred_binary)
print("Confusion Matrix:")
print(conf_matrix)

Let's visualise the same thing a bit better:

In [ ]:
conf_matrix = confusion_matrix(y_test, y_pred_binary)

# Create a heatmap
plt.figure(figsize=(6, 5))  # Size of the plot
sns.heatmap(conf_matrix, annot=True, fmt='g', cmap='Blues', cbar=False, 
            xticklabels=["Predicted Loss", "Predicted Win"], 
            yticklabels=["Actual Loss", "Actual Win"])
plt.title("Confusion Matrix Heatmap")
plt.xlabel("Predicted Label")
plt.ylabel("True Label")
plt.show()

Can you do the same on the training set? What do you notice?


What I have here is called a **confusion matrix**: it represents counts from predicted and actual values.

Perhaps, a bit of vocabulary to know in the context of binary classification:

-   the two classes in your classification are called positive class (i.e the class you're interested in, here match wins), and negative class

-   knowing that, you define true positives (TP) as the instances in your dataset that are of the positive class and are correctly classified by the model as belonging to the positive class, true negatives (TN) are the instances that are of the negative class and are correctly predicted by the model as belonging to the negative class, false positives (FP) are instances of the negative class that are misclassified by the model as instances of the positive class and false negatives (FN) are instances of the positive class that are falsely predicted by the model as belonging to the negative class

-   whether the FN or FP count is more important depends on your application

Now, let's have a look at a few more metrics:

In [ ]:
# Precision
precision = precision_score(y_test, y_pred_binary)
print("Precision:", precision)

# Recall
recall = recall_score(y_test, y_pred_binary)
print("Recall:", recall)

f1_score_test = f1_score(y_test, y_pred_binary)
print("F1 score:", f1_score_test)

# Accuracy
accuracy = accuracy_score(y_test, y_pred_binary)
print("Accuracy:", accuracy)

# Class Imbalance: Proportion of each class in the target variable
class_distribution = np.bincount(y_test) / len(y_test)
print("Class Imbalance (Proportions):")
print(f"Class 0 (Loss): {class_distribution[0]:.2f}, Class 1 (Win): {class_distribution[1]:.2f}")

-   Accuracy

    It's the proportion of correct predictions i.e

    $$
    \begin{equation}
    accuracy = \frac{TP+TN}{P+N}\
    \end{equation}
    $$

    where $P$ is the total number of positive instances in the dataset and $N$ the total number of negative instances in the dataset.

    It's only a good metric when the classes within your dataset are balanced. Can you guess what the problem might be in case of imbalance?

    How do you check if classes are balanced?

What about our data? The win class is over-represented!

So accuracy is **not** an appropriate metric in this case.

What metrics can we use in case of imbalance?

-   Precision, recall/sensitivity and F1-score

    Precision is the proportion of true positives among all the predicted positive cases.

    $$
    \begin{align}
    precision &= \frac{TP}{TP+FP}\\
              &= \frac{TP}{\textrm{all predicted positives}}
    \end{align}
    $$

    It is a good metric when the cost of false positives is high, e.g spam detection (the consequences of misclassifying a legitimate email as spam can be significant as it may result in important communications being filtered out and so the cost of a false positive is higher than that of a false negative in this case).

    Recall (or sensitivity) is the proportion of true positives among all actual positive cases.

    $$
    \begin{align}
    recall &= \frac{TP}{TP+FN}\\
              &= \frac{TP}{\textrm{all actual positives}}
    \end{align}
    $$

    High recall is critical in applications where the cost of false negatives is high, e.g medical applications. If you think back to this week's lab, a false negative meant a patient that had diabetes being misdiagnosed as being healthy resulting in delayed diagnosis and delayed appropriate treatment (and likely deterioration of the patient's condition in the meanwhile).

    Most applications, though, will need a balance between precision and recall. That's where the F-score (especially in the form of the balanced F1-score) comes in: it's the harmonic mean of precision and recall.

    $$
    \textrm{F1-score}=2\frac{precision * recall}{precision + recall}
    $$

    A more general score $F_\beta$ exists if you want to emphasize precision over recall or vice versa:

    $$
    \textrm{F}_{\beta}\textrm{-score} = (1+\beta^2)\frac{precision * recall}{(\beta^2.precision)+ recall}
    $$

-   Specificity

    The specificity is the proportion of negatives that are correctly identified as negatives.

    $$
    specificity = \frac{TN}{TN+FP}
    $$

    It is important in contexts where the classification of negatives is of high priority.

    It's particularly useful in the medical context. Consider the example of a medical test for diagnosing a disease; e.g the HbA1C blood test used to diagnose diabetes. Specificity refers to the test's ability to correctly reject healthy patients without the condition (i.e without diabetes). Supposing HbA1C had high specificity, a positive result in such test with high specificity would be useful for "ruling in" disease, i.e determining that the patient does in fact have diabetes, since the test rarely gives positive results in healthy patients.

-   Balanced accuracy

    But specificity is also used in another context. It is one of the components used to define balanced accuracy, a metric designed to overcome the problem that accuracy has when it comes to imbalanced data.

    $$
    \begin{equation}
    \textrm{balanced}\_\textrm{accuracy}= \frac{sensitivity+specificity}{2}
    \end{equation}
    $$

The closer the balanced accuracy is to 1, the better the model is able to correctly classify observations (for both classes).

**A recap of the metrics**

| **Metric** | **Description** |
|---------------------------------|--------------------------------------|
| Accuracy | Proportion of correct predictions |
| Sensitivity (=recall) | The proportion of positive results out of the number of samples that were actually positive. |
| Specificity | The proportion of negatives that are correctly identified as negatives. |
| Precision | The proportion of true positive results out of the number of samples that were predicted as positive. |
| Recall (=sensitivity) | The proportion of true positive results out of the number of samples that were actually positive. |
| F-measure | The harmonic mean of precision and recall. |
| Balanced accuracy | Mean of sensitivity and specificity |

# Part 2: Classifying differently: K-NN

## 2.1 The principles

**Basic idea (images and example from [here](https://www.analyticsvidhya.com/blog/2018/03/introduction-k-neighbours-algorithm-clustering/)):**

Look at this example. Say you want to predict the class of the blue star (BS) and see whether it's a red circle (RC) or a green square (GS).

![](images/paste-4.png)

$K$-NN will take "votes" from the nearest neighbours (nearest defined based on pre-specified distance usually Euclidian distance) and will only look at $K$ neighbours (hence the $K$ in $K$-NN).

In this case, if we take $K=3$, we see that the blue star is surrounded by 3 red circles and no green squares, so the star would be classified as a red circle.

![](images/paste-5.png)

**K-NN: the steps**

1.  Load the data

2.  Initialise the value of \$K\$

3.  To get the predicted class, iterate over the test data points

    -   Calculate the distance between test data point and each row of the training set. By default, use the Euclidian distance. Other distance metrics that could be used are the Manhattan distance, Minkowski distance, Chebyshev, cosine, etc. If there are categorical variables, the Hamming distance can be used.

    -   Sort the calculated distances in ascending order based on distance values

    -   Get top $K$ rows from the sorted array of distances

    -   Get the most frequent class from these rows

    -   Return the most frequent class as the predicted class for the current test data point

## 2.2 Applying it to our problem of predicting tennis match wins

How about we try $K$-NN to the same prediction problem as before: predicting tennis match wins

In [ ]:
knn = KNeighborsClassifier(n_neighbors=3)

Let's evaluate the model now, first on the training set then the test set:

In [ ]:
knn.fit(X, y)

y_pred_train_knn = knn.predict(X)
# Predict on test data
y_pred_knn = knn.predict(X_test)

# Display results
print("Predicted Rounds (Encoded):", y_pred_knn)
print("Actual Rounds (Encoded):", y_test.values)

In [ ]:
y_pred_train_binary_knn = (y_pred_train_knn > 0.5).astype(int)

# Confusion Matrix
conf_matrix_train_knn = confusion_matrix(y, y_pred_train_binary_knn)
print("Confusion Matrix (training set):")
print(conf_matrix_train_knn)

# Precision
precision_train_knn = precision_score(y, y_pred_train_binary_knn)
print("Precision (training set):", precision_train_knn)

# Recall
recall_train_knn = recall_score(y, y_pred_train_binary_knn)
print("Recall (training set):", recall_train_knn)

# Accuracy
f1_score_train_knn = f1_score(y, y_pred_train_binary_knn)
print("F1 score (training set):", f1_score_train_knn)

balanced_accuracy_train_knn = balanced_accuracy_score(y, y_pred_train_binary_knn)
print("Balanced accuracy (training set):", balanced_accuracy_train_knn)

# Class Imbalance: Proportion of each class in the target variable
class_distribution_train = np.bincount(y) / len(y)
print("Class Imbalance (Proportions) (training set):")
print(f"Class 0 (Loss): {class_distribution_train[0]:.2f}, Class 1 (Win): {class_distribution_train[1]:.2f}")

In [ ]:
y_pred_binary_knn = (y_pred_knn > 0.5).astype(int)

# Confusion Matrix
conf_matrix_knn = confusion_matrix(y_test, y_pred_binary_knn)
print("Confusion Matrix:")
print(conf_matrix_knn)

# Precision
precision_knn = precision_score(y_test, y_pred_binary_knn)
print("Precision:", precision_knn)

# Recall
recall_knn = recall_score(y_test, y_pred_binary_knn)
print("Recall:", recall_knn)

# Accuracy
f1_score_test_knn = f1_score(y_test, y_pred_binary_knn)
print("F1 score:", f1_score_test_knn)

balanced_accuracy_knn = balanced_accuracy_score(y_test, y_pred_binary_knn)
print("Balanced accuracy:", balanced_accuracy_knn)

# Class Imbalance: Proportion of each class in the target variable
class_distribution = np.bincount(y_test) / len(y_test)
print("Class Imbalance (Proportions):")
print(f"Class 0 (Loss): {class_distribution[0]:.2f}, Class 1 (Win): {class_distribution[1]:.2f}")

How does $K$-NN compare to logistic regression?

📚 **Notes**: When independent variables in training data are measured in different units, it is important to standardize variables before calculating distance. So, it is usually good practice to normalize the dataset before applying $K$-NN. You can do that with `StandardScaler` for example. You can have a look at [this page](https://www.geeksforgeeks.org/how-to-standardize-data-in-a-pandas-dataframe/) to see ways to standardize your data.

Because it relies on distance calculations, $K$-NN is sensitive to outliers

🎯 ACTION POINT: How should I go about modifying my $K$-NN model and its evaluation?
